In [ ]:
#整个过程是参考的tensorflow BERT官网实现https://github.com/google-research/bert，
#以及一个外国工程师基于官网实现做的horovod分布式处理BERT finetuning的实现https://github.com/lambdal/bert

In [ ]:
#整个过程包括几个步骤：
#1. 准备数据
#2. 准备预训练好的BERT模型
#3. 准备clone github的代码
#4. 在本地测试基于BERT模型的finetuning的文本分类任务。
#5. 将代码迁移到Sagemaker中，并利用horovod进行多机多卡的分布式训练

In [ ]:
#1. 利用官网提供的脚本来下载数据
#步骤是：下载脚本；利用这个脚本下载数据；解压数据

In [1]:
!wget https://gist.github.com/W4ngatang/60c2bdb54d156a41194446737ce03e2e/archive/17b8dd0d724281ed7c3b2aeeda662b92809aadd5.zip

--2020-06-30 12:24:48--  https://gist.github.com/W4ngatang/60c2bdb54d156a41194446737ce03e2e/archive/17b8dd0d724281ed7c3b2aeeda662b92809aadd5.zip
Resolving gist.github.com (gist.github.com)... 140.82.112.4
Connecting to gist.github.com (gist.github.com)|140.82.112.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://codeload.github.com/gist/60c2bdb54d156a41194446737ce03e2e/zip/17b8dd0d724281ed7c3b2aeeda662b92809aadd5 [following]
--2020-06-30 12:24:48--  https://codeload.github.com/gist/60c2bdb54d156a41194446737ce03e2e/zip/17b8dd0d724281ed7c3b2aeeda662b92809aadd5
Resolving codeload.github.com (codeload.github.com)... 140.82.112.10
Connecting to codeload.github.com (codeload.github.com)|140.82.112.10|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3403 (3.3K) [application/zip]
Saving to: ‘17b8dd0d724281ed7c3b2aeeda662b92809aadd5.zip’

17b8dd0d724281ed7c3 100%[===================>]   3.32K  --.-KB/s    in 0s      

2020-06-30 12

In [2]:
!unzip 17b8dd0d724281ed7c3b2aeeda662b92809aadd5.zip

Archive:  17b8dd0d724281ed7c3b2aeeda662b92809aadd5.zip
17b8dd0d724281ed7c3b2aeeda662b92809aadd5
   creating: 60c2bdb54d156a41194446737ce03e2e-17b8dd0d724281ed7c3b2aeeda662b92809aadd5/
  inflating: 60c2bdb54d156a41194446737ce03e2e-17b8dd0d724281ed7c3b2aeeda662b92809aadd5/download_glue_data.py  


In [3]:
!python 60c2bdb54d156a41194446737ce03e2e-17b8dd0d724281ed7c3b2aeeda662b92809aadd5/download_glue_data.py --data_dir glue_data --tasks all

	Completed!
	Completed!
Processing MRPC...
Local MRPC data not specified, downloading data from https://dl.fbaipublicfiles.com/senteval/senteval_data/msr_paraphrase_train.txt
	Completed!
	Completed!
	Completed!
	Completed!
	Completed!
	Completed!
	Completed!
	Completed!
	Completed!


In [ ]:
#2. 准备预训练好的BERT模型
#这里使用的是全部小写化的large模型：下载预训练的BERT模型并解压

In [4]:
!wget -q https://storage.googleapis.com/bert_models/2018_10_18/uncased_L-12_H-768_A-12.zip

In [5]:
!unzip uncased_L-12_H-768_A-12.zip

Archive:  uncased_L-12_H-768_A-12.zip
   creating: uncased_L-12_H-768_A-12/
  inflating: uncased_L-12_H-768_A-12/bert_model.ckpt.meta  
  inflating: uncased_L-12_H-768_A-12/bert_model.ckpt.data-00000-of-00001  
  inflating: uncased_L-12_H-768_A-12/vocab.txt  
  inflating: uncased_L-12_H-768_A-12/bert_model.ckpt.index  
  inflating: uncased_L-12_H-768_A-12/bert_config.json  


In [ ]:
#3. 准备clone github的代码
#在sagemaker jupyter lab中对应的项目目录中创建source_code目录，
#然后选择git按钮输入https://github.com/lambdal/bert.git

In [6]:
#4. 在本地测试基于BERT模型的finetuning的文本分类任务。
#注意下面的一些参数： data_dir是需要使用的数据集，voca_file是需要用到的词典（来自上一步解压后的一个文件）
#                  bert_config_file是bert的配置文件，init_checkpoint是预训练好的BERT模型。
#                  output_dir是训练过程中的checkpoint保存的路径。

In [9]:
!python ./source_code/bert/run_classifier.py \
  --task_name=MRPC \
  --do_train=true \
  --do_eval=true \
  --data_dir=./glue_data/MRPC \
  --vocab_file=./uncased_L-12_H-768_A-12/vocab.txt \
  --bert_config_file=./uncased_L-12_H-768_A-12/bert_config.json \
  --init_checkpoint=./uncased_L-12_H-768_A-12/bert_model.ckpt \
  --max_seq_length=128 \
  --train_batch_size=32 \
  --learning_rate=2e-5 \
  --num_train_epochs=1.0 \
  --output_dir=./mrpc_output/




W0630 12:49:40.929617 139916696061760 module_wrapper.py:139] From ./source_code/bert/run_classifier.py:784: The name tf.logging.set_verbosity is deprecated. Please use tf.compat.v1.logging.set_verbosity instead.


W0630 12:49:40.929754 139916696061760 module_wrapper.py:139] From ./source_code/bert/run_classifier.py:784: The name tf.logging.INFO is deprecated. Please use tf.compat.v1.logging.INFO instead.


W0630 12:49:40.930103 139916696061760 module_wrapper.py:139] From /home/ec2-user/SageMaker/bert with TF/horovod bert with TF/source_code/bert/modeling.py:92: The name tf.gfile.GFile is deprecated. Please use tf.io.gfile.GFile instead.


W0630 12:49:40.930678 139916696061760 module_wrapper.py:139] From ./source_code/bert/run_classifier.py:808: The name tf.gfile.MakeDirs is deprecated. Please use tf.io.gfile.makedirs instead.

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/maste

In [ ]:
#5. 将代码迁移到Sagemaker中，并利用horovod进行多机多卡的分布式训练

In [ ]:
#5.1 把预训练的包解压完的所有文件拷贝到source_code/bert目录下。
#这样做的原因是在使用Sagemaker BYOS来训练的时候，训练脚本依赖的所有source code，配置文件，资源文件都需要和训练脚本在同一级的目录。

In [11]:
!cp uncased_L-12_H-768_A-12/* source_code/bert/

In [ ]:
#5.2 把数据集上传到AWS的S3的桶（桶要提前建立）

In [12]:
!aws s3 sync glue_data/MRPC s3://sagemaker-us-east-1-514385905925/bert-SM-TF-test

upload: glue_data/MRPC/dev_ids.tsv to s3://sagemaker-us-east-1-514385905925/bert-SM-TF-test/dev_ids.tsv
upload: glue_data/MRPC/dev.tsv to s3://sagemaker-us-east-1-514385905925/bert-SM-TF-test/dev.tsv
upload: glue_data/MRPC/test.tsv to s3://sagemaker-us-east-1-514385905925/bert-SM-TF-test/test.tsv
upload: glue_data/MRPC/msr_paraphrase_train.txt to s3://sagemaker-us-east-1-514385905925/bert-SM-TF-test/msr_paraphrase_train.txt
upload: glue_data/MRPC/.ipynb_checkpoints/msr_paraphrase_train-checkpoint.txt to s3://sagemaker-us-east-1-514385905925/bert-SM-TF-test/.ipynb_checkpoints/msr_paraphrase_train-checkpoint.txt
upload: glue_data/MRPC/msr_paraphrase_test.txt to s3://sagemaker-us-east-1-514385905925/bert-SM-TF-test/msr_paraphrase_test.txt
upload: glue_data/MRPC/.ipynb_checkpoints/train-checkpoint.tsv to s3://sagemaker-us-east-1-514385905925/bert-SM-TF-test/.ipynb_checkpoints/train-checkpoint.tsv
upload: glue_data/MRPC/train.tsv to s3://sagemaker-us-east-1-514385905925/bert-SM-TF-test/trai

In [ ]:
#5.3 把训练脚本以及依赖的配置文件，资源文件（这里指的是预训练的模型文件）上传到S3的桶
#其实不上传也没有问题，但是每次在开始训练前sagemaker都要重新对这些文件打包上传，影响训练启动速度。
#因此最好的方式就是提前打包上传到S3.
#把原来bert目录下的requirements.txt文件换个名字，否则Sagemaker会安装这个文件中的软件包（这里我们不需要安装任何软件包了）

In [18]:
!mv source_code/bert/requirements.txt source_code/bert/requirements.txt.copy

In [19]:
%%script bash
cd source_code/bert
tar cvfz sourcedir.tar.gz *
aws s3 cp sourcedir.tar.gz s3://liang200/bert-hvd-tf/

bert_config.json
bert_model.ckpt.data-00000-of-00001
bert_model.ckpt.index
bert_model.ckpt.meta
CONTRIBUTING.md
create_pretraining_data.py
extract_features.py
__init__.py
LICENSE
modeling.py
modeling_test.py
multilingual.md
optimization_hvd.py
optimization.py
optimization_test.py
__pycache__/
__pycache__/modeling.cpython-36.pyc
__pycache__/tokenization.cpython-36.pyc
__pycache__/optimization.cpython-36.pyc
README.md
requirements.txt.copy
run_classifier_hvd.py
run_classifier.py
run_pretraining_hvd.py
run_pretraining.py
run_squad_hvd.py
run_squad.py
sample_text.txt
tokenization.py
tokenization_test.py
vocab.txt
upload: ./sourcedir.tar.gz to s3://liang200/bert-hvd-tf/sourcedir.tar.gz


In [ ]:
#5.4 调用Sagemaker的API开始finetuning

In [ ]:
#这里是使用horovod多机多卡训练，使用的是ml.p3.8xlarge（4个GPU卡），所以需要设置每个实例的worker数量为4
#为了节省成本，这里使用spot实例来训练。
#参数output_dir需要设置为/opt/ml/model，只有在这个路径下，sagemaker训练完才会把这个路径下的所有文件打包并上传。
#参数data_dir需要设置为/opt/ml/input/data/training/，sagemaker file mode训练方式会把数据下载到这个目录，最后一级目录的名字（这里是training）需要和你的S3的channel的名字保持一致
#参数do_train和do_eval需要设置为1，不能写True或者true，因为SM中使用hyperparameter对自己的脚本输入参数的时候，SM会把所有的参数都字符串化。
#参数vocab_file，bert_config_file和init_checkpoint的路径前缀都是/opt/ml/code/，这个是因为sagemaker会把训练脚本以及所有依赖的源代码，配置文件，资源文件等都拷贝到这个目录。
#entry_point设置为run_classifier_hvd.py进行分布式训练，这个脚本中已经写成了horovod集成tensorflow的方式。
#source_dir参数指向指向打包代码以及依赖上传到S3的路径。
#train_volume_size设置大一些（不一定像我下面设置的1TB这么大），否则模型在训练过程中保存checkpoint或者在训练完打包这些checkpoint上传S3的时候可能硬盘空间不够。

In [22]:
import sagemaker
from sagemaker.tensorflow import TensorFlow

train_instance_type = 'ml.p3.8xlarge'
hvd_processes_per_host = 4
distributions = {'mpi': {
                    'enabled': True,
                    'processes_per_host': hvd_processes_per_host,
                    'custom_mpi_options': '-verbose --NCCL_DEBUG=INFO -x OMPI_MCA_btl_vader_single_copy_mechanism=none'
                        }
                }

train_use_spot_instances = True
train_max_run=432000 #这个是AWS账号默认的最大训练时间，可以通过联系AWS售后提升整个limit。
train_max_wait = 432000 if train_use_spot_instances else None


hyperparameters = {'output_dir': '/opt/ml/model', 'data_dir': '/opt/ml/input/data/training/',
                   'do_train': 1, 'do_eval': 1,
                   'vocab_file': '/opt/ml/code/vocab.txt', 
                   'bert_config_file': '/opt/ml/code/bert_config.json', 
                   'init_checkpoint': '/opt/ml/code/bert_model.ckpt',
                   'num_train_epochs': 100.0, 'train_batch_size': 32, 'max_seq_length': 128, 'learning_rate': 2e-5, 
                   'task_name':'MRPC'}

estimator = TensorFlow(entry_point='run_classifier_hvd.py',
                       source_dir='s3://liang200/bert-hvd-tf/sourcedir.tar.gz',
                       train_instance_type=train_instance_type,
                       train_instance_count=2,
                       train_volume_size=1000,
                       hyperparameters=hyperparameters,
                       role=sagemaker.get_execution_role(),
                       base_job_name='tf-bert-sm-test',
                       framework_version='1.14',
                       py_version='py3',
                       script_mode=True,
                       distributions=distributions,
                       train_use_spot_instances=train_use_spot_instances,
                       train_max_wait=train_max_wait,
                       train_max_run=train_max_run
                       )

In [23]:
train_s3 = 's3://sagemaker-us-east-1-514385905925/bert-SM-TF-test'
train_channel = 'training'

inputs = {train_channel: train_s3}

estimator.fit(inputs)

2020-06-30 15:52:33 Starting - Starting the training job...
2020-06-30 15:52:35 Starting - Launching requested ML instances.........
2020-06-30 15:54:22 Starting - Preparing the instances for training.........
2020-06-30 15:56:03 Downloading - Downloading input data
2020-06-30 15:56:03 Training - Downloading the training image...
2020-06-30 15:56:28 Training - Training image download completed. Training in progress../usr/local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/usr/local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8